# EDA on NYC Taxi Tip Data

In [0]:
# Load data
from pyspark.sql import SparkSession

spark = SparkSession.builder.appName("NYC Taxi Tip EDA").getOrCreate()
df = spark.read.csv("/FileStore/tables/NYC_Taxi_Trip_Record_Clean.csv", header=True, inferSchema=True)
df.cache()

Out[52]: DataFrame[lpep_pickup_datetime: string, lpep_dropoff_datetime: string, day_category: string, pickup_time: string, RatecodeID: string, PULocationID: int, PUBorough: string, PUZone: string, DOLocationID: int, DOBorough: string, DOZone: string, passenger_count: string, trip_distance: double, distance_bins: string, fare_amount: double, fare_amount_bins: string, tip_amount: double, tip_amount_bins: string, payment_type: string, trip_type: string, trip_duration: double, duration_bins: string, speed: double, speed_bins: string]

In [0]:
# 2. 
df.printSchema()

root
 |-- lpep_pickup_datetime: string (nullable = true)
 |-- lpep_dropoff_datetime: string (nullable = true)
 |-- day_category: string (nullable = true)
 |-- pickup_time: string (nullable = true)
 |-- RatecodeID: string (nullable = true)
 |-- PULocationID: integer (nullable = true)
 |-- PUBorough: string (nullable = true)
 |-- PUZone: string (nullable = true)
 |-- DOLocationID: integer (nullable = true)
 |-- DOBorough: string (nullable = true)
 |-- DOZone: string (nullable = true)
 |-- passenger_count: string (nullable = true)
 |-- trip_distance: double (nullable = true)
 |-- distance_bins: string (nullable = true)
 |-- fare_amount: double (nullable = true)
 |-- fare_amount_bins: string (nullable = true)
 |-- tip_amount: double (nullable = true)
 |-- tip_amount_bins: string (nullable = true)
 |-- payment_type: string (nullable = true)
 |-- trip_type: string (nullable = true)
 |-- trip_duration: double (nullable = true)
 |-- duration_bins: string (nullable = true)
 |-- speed: double (n

In [0]:

df.show(5)

+--------------------+---------------------+------------+-----------+-------------+------------+---------+-------------------+------------+---------+--------------------+---------------+-------------+-------------+-----------+----------------+----------+---------------+------------+-----------+-------------+-------------+-----+----------+
|lpep_pickup_datetime|lpep_dropoff_datetime|day_category|pickup_time|   RatecodeID|PULocationID|PUBorough|             PUZone|DOLocationID|DOBorough|              DOZone|passenger_count|trip_distance|distance_bins|fare_amount|fare_amount_bins|tip_amount|tip_amount_bins|payment_type|  trip_type|trip_duration|duration_bins|speed|speed_bins|
+--------------------+---------------------+------------+-----------+-------------+------------+---------+-------------------+------------+---------+--------------------+---------------+-------------+-------------+-----------+----------------+----------+---------------+------------+-----------+-------------+---------

In [0]:

df.count()

Out[55]: 60698

In [0]:
# 5. Get summary statistics (count, mean, stddev, min, max) of numeric columns?

display(df.describe())

summary lpep_pickup_datetime lpep_dropoff_datetime day_category pickup_time RatecodeID PULocationID PUBorough PUZone DOLocationID DOBorough DOZone passenger_count trip_distance distance_bins fare_amount fare_amount_bins tip_amount tip_amount_bins payment_type trip_type trip_duration duration_bins speed speed_bins count 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 60698 mean null null null null null 97.28895515502983 null null 139.7581633661735 null null 1.1081666233653762 2.9098363208013485 null 16.772223796500782 null 2.2597301393785663 null null null 14.051646017990734 null 12.11560463277198 null stddev null null null null null 59.656318498654784 null null 76.07590197793792 null null 0.3549895606902233 2.6465367616248243 null 10.834099451817593 null 2.7108688030516888 null null null 9.253346907328678 null 5.151361349206878 null min 01-01-2023 0.01 01-01-2023 0.13 Weekdays Evening JFK Airport 3 Bronx Allerton/Pelham Gardens 1 Bronx Allerton/Pelham Gardens 1 0.63 3-6 miles 2.5 21-40$ 0.0 0$ Cash Dispatch 2.02 11-20 minutes 5.0 11-20 mph max 31-01-2023 9.58 31-01-2023 9.59 Weekend Noon Standard rate 263 Staten Island Yorkville West 263 Staten Island Yorkville West >3 41.74 >10 miles 161.2 >60$ 50.0 >15$ Unknown Street-hail 172.48 >30 minutes 60.05 >30 mph

In [0]:
# 6. Calculate average tip amount grouped by passenger count
# TODO: Write the code to answer the above question
from pyspark.sql.functions import *
display(df.groupBy('passenger_count').agg(avg('tip_amount').alias('Avg Tip Amount')))

passenger_count Avg Tip Amount 3 2.309636576787808 1 2.2478845308828332 >3 2.434799190010125 2 2.2726701916721734

In [0]:
# 7. Calculate total tip amount by payment type
# TODO: Write the code to answer the above question
display(df.groupBy('payment_type').agg(sum('tip_amount').alias('Total Tip Amount')))

payment_type Total Tip Amount Cash 0.0 Dispute 0.0 No charge 0.0 Credit card 137161.1000000002 Unknown 0.0

In [0]:
# 8. Display records where the tip amount is greater than 5
# TODO: Write the code to answer the above question
display(df.filter(col('tip_amount')>5))

lpep_pickup_datetime lpep_dropoff_datetime day_category pickup_time RatecodeID PULocationID PUBorough PUZone DOLocationID DOBorough DOZone passenger_count trip_distance distance_bins fare_amount fare_amount_bins tip_amount tip_amount_bins payment_type trip_type trip_duration duration_bins speed speed_bins 01-01-2023 0.40 01-01-2023 1.04 Weekend Midnight Negotiated fare 66 Brooklyn DUMBO/Vinegar Hill 164 Manhattan Midtown South >3 6.78 7-10 miles 60.0 41-60$ 12.61 11-15$ Credit card Dispatch 23.57 21-30 minutes 17.26 11-20 mph 01-01-2023 0.46 01-01-2023 0.59 Weekend Midnight Standard rate 75 Manhattan East Harlem South 143 Manhattan Lincoln Square West 1 3.19 3-6 miles 15.6 <20$ 6.26 6-10$ Credit card Street-hail 13.03 11-20 minutes 14.69 11-20 mph 01-01-2023 0.23 01-01-2023 0.47 Weekend Midnight Standard rate 255 Brooklyn Williamsburg (North Side) 48 Manhattan Clinton East 1 8.55 7-10 miles 47.8 41-60$ 5.3 6-10$ Credit card Street-hail 24.58 21-30 minutes 20.87 21-30 mph 01-01-2023 0.34 01-01-2023 0.50 Weekend Midnight Standard rate 130 Queens Jamaica 196 Queens Rego Park 1 4.46 3-6 miles 21.2 21-40$ 7.11 6-10$ Credit card Street-hail 15.9 11-20 minutes 16.83 11-20 mph 01-01-2023 0.11 01-01-2023 0.38 Weekend Midnight Standard rate 65 Brooklyn Downtown Brooklyn/MetroTech 162 Manhattan Midtown East 2 7.3 7-10 miles 25.5 21-40$ 7.55 6-10$ Credit card Street-hail 27.0 21-30 minutes 16.22 11-20 mph 01-01-2023 1.11 01-01-2023 1.41 Weekend Midnight Standard rate 152 Manhattan Manhattanville 140 Manhattan Lenox Hill East 2 4.9 3-6 miles 26.8 21-40$ 6.41 6-10$ Credit card Street-hail 29.7 21-30 minutes 9.9 <10 mph 01-01-2023 1.23 01-01-2023 1.53 Weekend Midnight Standard rate 255 Brooklyn Williamsburg (North Side) 249 Manhattan West Village 1 4.9 3-6 miles 29.6 21-40$ 8.71 6-10$ Credit card Street-hail 30.13 >30 minutes 9.76 <10 mph 01-01-2023 1.34 01-01-2023 2.00 Weekend Midnight Standard rate 260 Queens Woodside 262 Manhattan Yorkville East 1 5.2 3-6 miles 28.2 21-40$ 6.69 6-10$ Credit card Street-hail 25.42 21-30 minutes 12.27 11-20 mph 01-01-2023 1.34 01-01-2023 1.52 Weekend Midnight Standard rate 166 Manhattan Morningside Heights 229 Manhattan Sutton Place/Turtle Bay North 2 5.13 3-6 miles 25.4 21-40$ 7.66 6-10$ Credit card Street-hail 18.45 11-20 minutes 16.68 11-20 mph 01-01-2023 1.39 01-01-2023 2.00 Weekend Midnight Standard rate 75 Manhattan East Harlem South 95 Queens Forest Hills 1 11.34 >10 miles 44.3 41-60$ 6.65 6-10$ Credit card Street-hail 21.65 21-30 minutes 31.43 >30 mph 01-01-2023 1.41 01-01-2023 1.56 Weekend Midnight Standard rate 112 Brooklyn Greenpoint 237 Manhattan Upper East Side South 1 4.08 3-6 miles 20.5 21-40$ 6.44 6-10$ Credit card Street-hail 15.63 11-20 minutes 15.66 11-20 mph 01-01-2023 1.23 01-01-2023 1.54 Weekend Midnight Standard rate 66 Brooklyn DUMBO/Vinegar Hill 41 Manhattan Central Harlem 1 10.96 >10 miles 46.4 41-60$ 10.33 11-15$ Credit card Street-hail 30.95 >30 minutes 21.25 21-30 mph 01-01-2023 1.57 01-01-2023 2.15 Weekend Midnight Standard rate 80 Brooklyn East Williamsburg 223 Queens Steinway 1 6.81 7-10 miles 29.6 21-40$ 6.42 6-10$ Credit card Street-hail 17.75 11-20 minutes 23.02 21-30 mph 01-01-2023 1.20 01-01-2023 1.41 Weekend Midnight Standard rate 33 Brooklyn Brooklyn Heights 237 Manhattan Upper East Side South 1 8.07 7-10 miles 33.8 21-40$ 7.81 6-10$ Credit card Street-hail 20.95 21-30 minutes 23.11 21-30 mph 01-01-2023 2.28 01-01-2023 2.42 Weekend Midnight Standard rate 66 Brooklyn DUMBO/Vinegar Hill 80 Brooklyn East Williamsburg 1 3.5 3-6 miles 17.7 <20$ 6.06 6-10$ Credit card Street-hail 13.9 11-20 minutes 15.11 11-20 mph 01-01-2023 2.50 01-01-2023 3.04 Weekend Midnight Standard rate 255 Brooklyn Williamsburg (North Side) 181 Brooklyn Park Slope 1 6.39 7-10 miles 26.8 21-40$ 8.79 6-10$ Credit card Street-hail 13.85 11-20 minutes 27.68 21-30 mph 01-01-2023 2.55 01-01-2023 3.09 Weekend Midnight Standard rate 75 Manhattan East Harlem South 162 Manhattan Midtown East 1 3.92 3-6 miles 19

In [0]:
# 9. Identify outliers where tip amount is greater than 50?
# TODO: Write the code to answer the above question
display(df.filter(col('tip_amount')>50))

lpep_pickup_datetime lpep_dropoff_datetime day_category pickup_time RatecodeID PULocationID PUBorough PUZone DOLocationID DOBorough DOZone passenger_count trip_distance distance_bins fare_amount fare_amount_bins tip_amount tip_amount_bins payment_type trip_type trip_duration duration_bins speed speed_bins

In [0]:
# 10. How to calculate the correlation between trip distance and tip amount?
# TODO: Write the code to answer the above question


display(df.groupBy('trip_distance').agg(sum('tip_amount')))
df.corr('tip_amount','trip_distance')

trip_distance sum(tip_amount) 0.66 102.92000000000002 15.5 0.0 2.86 201.28 3.26 114.72 13.4 18.82 10.65 17.27 8.51 33.66 9.13 8.01 1.82 303.67999999999995 6.96 84.67 16.54 0.0 15.4 12.52 9.55 24.23 15.92 0.0 5.86 37.44 0.84 243.54999999999998 5.05 109.17 2.4 629.97 5.78 89.97 14.18 15.98 4.19 120.15000000000002 9.72 17.689999999999998 18.78 31.22 5.13 85.37 9.49 23.08 2.41 253.93 1.41 410.77999999999986 5.48 45.190000000000005 2.82 163.02000000000004 8.0 74.32000000000001 10.82 41.60000000000001 2.62 222.51 5.76 77.36 7.91 77.03999999999999 9.41 12.84 18.3 32.22 0.87 259.56999999999994 6.17 55.730000000000004 6.44 15.38 4.88 62.47 8.75 16.81 8.83 17.48 8.31 28.54 3.02 185.65999999999997 7.39 42.650000000000006 27.61 8.88 4.92 87.23 11.45 0.0 14.87 0.0 14.11 19.0 5.4 204.64 1.42 423.2799999999999 2.55 285.02 4.23 102.94 7.42 79.74000000000001 12.89 27.71 12.79 11.79 16.6 0.0 6.27 35.29 1.31 282.67999999999995 11.14 30.66 4.02 116.35 6.43 34.769999999999996 7.0 102.28 19.11 0.0 1.16 272.97999999999996 3.08 197.48000000000002 4.36 130.28 8.97 45.13 8.48 28.07 15.9 20.0 15.48 0.0 9.34 28.910000000000004 3.57 105.42000000000002 12.43 9.0 0.93 198.59000000000006 4.93 94.08000000000001 12.85 10.0 11.5 14.4 7.84 32.58 3.5 334.4 3.56 76.5 2.28 285.09000000000003 6.37 50.66 6.1 95.19 17.58 0.0 8.99 20.270000000000003 9.5 69.81 16.39 15.0 5.34 89.91 2.64 239.13 1.69 260.59000000000003 0.89 201.54000000000005 8.79 31.53 4.34 87.2 11.27 10.94 3.33 172.40000000000003 11.6 17.36 8.36 31.019999999999996 14.69 13.55 8.55 41.21 11.08 43.190000000000005 3.88 129.02999999999997 8.54 9.23 11.66 0.0 3.19 133.64 2.84 194.93 7.7 123.73 3.93 163.14000000000001 8.85 9.93 6.41 64.35 2.97 215.88000000000005 3.45 138.38 7.36 101.58 10.69 10.8 17.79 1.95 2.02 296.38000000000005 1.08 304.11999999999995 2.79 265.72 3.35 110.93000000000002 1.25 244.76999999999998 17.3 31.21 12.28 0.0 9.78 8.68 10.88 23.54 1.44 297.36 5.45 46.83 1.54 365.65999999999997 2.85 244.35 11.62 5.0 6.6 148.73999999999998 5.47 69.9 1.89 295.52 3.64 160.67000000000002 10.05 21.11 26.74 0.0 9.97 20.490000000000002 13.81 11.68 5.95 27.75 3.65 171.47000000000006 2.63 233.61 3.42 149.56 8.71 56.230000000000004 8.06 128.82 8.29 25.36 18.93 16.21 1.72 321.96999999999997 10.54 26.72 4.41 108.5 19.01 16.77 13.54 34.29 7.01 86.55 8.7 105.33000000000001 13.3 12.45 10.03 31.470000000000002 5.84 74.16 10.71 21.240000000000002 2.9 542.3999999999999 1.63 264.31 5.88 51.190000000000005 16.84 0.0 12.12 13.89 6.66 68.78 16.89 0.0 6.91 45.68000000000001 15.1 25.37 7.22 61.53 10.78 7.52 3.23 154.52 5.42 98.49000000000001 3.7 318.65000000000003 4.27 109.08999999999999 5.69 61.449999999999996 5.11 97.21 6.28 69.4 10.56 44.129999999999995 18.61 17.01 12.5 23.060000000000002 1.52 386.2799999999999 2.35 292.88000000000005 3.62 152.07 2.94 214.7 3.96 150.13 6.54 55.35000000000001 11.64 9.0 13.78 11.54 4.5 264.86 10.3 34.41 8.93 33.49 3.66 153.7 1.94 328.55 9.99 18.59 7.03 74.72 26.75 12.0 10.13 17.14 3.11 203.01999999999998 2.61 247.66 17.47 15.61 8.15 65.16 5.01 71.05 18.65 0.0 2.21 250.73999999999998 5.7 194.25999999999996 4.39 100.66999999999999 10.94 25.869999999999997 13.07 28.72 1.4 920.0800000000003 7.94 41.17 4.56 115.88000000000001 5.74 54.739999999999995 17.36 0.0 0.79 121.30000000000001 5.56 76.28 4.53 103.77000000000001 7.88 43.44 16.11 11.22 7.06 47.050000000000004 7.96 47.25 1.05 264.0199999999999 0.72 154.59 5.66 47.71 2.27 286.23999999999995 6.73 69.17 5.63 142.07999999999998 10.37 18.52 7.62 44.480000000000004 14.52 27.13 5.62 35.21 10.59 38.38 11.21 0.0 1.7 713.5500000000002 3.01 156.75 4.49 73.4 6.7 125.96 7.65 50.14 9.25 34.95 9.81 0.0 5.96 29.32 2.34 288.37000000000006 6.09 78.13 4.06 102.91 18.47 32.75 0.7 309.88999999999993 15.8 51.28 8.28 106.03999999999999 2.3 622.62 4.33 63.370000000000005 2.96 216.56000000000003 7.4 122.5 11.93 0.0 4.08 125.45 8.76 28.689999999999998 1.49 317.05999999999995 6.69 92.42 16.58 0.0 13.62 36.480000000000004 6.5 194.52 13.8 26.94 12.26 3.0 10.87 22.15 8.18 

Out[61]: 0.4165306370446275

In [0]:
df1 = df.withColumn("lpep_pickup_datetime", col("lpep_pickup_datetime").cast("timestamp"))

# Extract day of the week
df1 = df1.withColumn("day_of_week", date_format(col("lpep_pickup_datetime"), "EEEE"))

display(df1.limit(100))

lpep_pickup_datetime lpep_dropoff_datetime day_category pickup_time RatecodeID PULocationID PUBorough PUZone DOLocationID DOBorough DOZone passenger_count trip_distance distance_bins fare_amount fare_amount_bins tip_amount tip_amount_bins payment_type trip_type trip_duration duration_bins speed speed_bins day_of_week null 01-01-2023 0.37 Weekend Midnight Standard rate 166 Manhattan Morningside Heights 143 Manhattan Lincoln Square West 1 2.58 3-6 miles 14.9 <20$ 4.03 1-5$ Credit card Street-hail 11.02 11-20 minutes 14.05 11-20 mph null null 01-01-2023 0.57 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 43 Manhattan Central Park 1 1.81 <2 miles 10.7 <20$ 2.64 1-5$ Credit card Street-hail 6.77 <10 minutes 16.04 11-20 mph null null 01-01-2023 0.19 Weekend Midnight Standard rate 41 Manhattan Central Harlem 238 Manhattan Upper West Side North 1 1.3 <2 miles 6.5 <20$ 1.7 1-5$ Credit card Street-hail 5.82 <10 minutes 13.4 11-20 mph null null 01-01-2023 0.39 Weekend Midnight Standard rate 41 Manhattan Central Harlem 74 Manhattan East Harlem North 1 1.1 <2 miles 6.0 <20$ 0.0 0$ Credit card Street-hail 5.97 <10 minutes 11.06 11-20 mph null null 01-01-2023 1.11 Weekend Midnight Standard rate 41 Manhattan Central Harlem 262 Manhattan Yorkville East 1 2.78 3-6 miles 17.7 <20$ 0.0 0$ Cash Street-hail 17.55 11-20 minutes 9.5 <10 mph null null 01-01-2023 0.26 Weekend Midnight Standard rate 181 Brooklyn Park Slope 45 Manhattan Chinatown 2 3.8 3-6 miles 19.1 <20$ 4.85 1-5$ Credit card Street-hail 17.42 11-20 minutes 13.09 11-20 mph null null 01-01-2023 0.24 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 75 Manhattan East Harlem South 1 1.88 <2 miles 14.2 <20$ 0.0 0$ Cash Street-hail 12.95 11-20 minutes 8.71 <10 mph null null 01-01-2023 0.46 Weekend Midnight Standard rate 41 Manhattan Central Harlem 166 Manhattan Morningside Heights 2 1.11 <2 miles 7.2 <20$ 1.0 1-5$ Credit card Street-hail 4.95 <10 minutes 13.45 11-20 mph null null 01-01-2023 1.13 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 140 Manhattan Lenox Hill East 1 4.22 3-6 miles 24.7 21-40$ 3.0 1-5$ Credit card Street-hail 23.17 21-30 minutes 10.93 11-20 mph null null 01-01-2023 0.41 Weekend Midnight Standard rate 255 Brooklyn Williamsburg (North Side) 234 Manhattan Union Sq 2 4.8 3-6 miles 26.8 21-40$ 0.0 0$ Credit card Street-hail 25.52 21-30 minutes 11.29 11-20 mph null null 01-01-2023 0.17 Weekend Midnight Standard rate 75 Manhattan East Harlem South 140 Manhattan Lenox Hill East 1 1.99 <2 miles 11.4 <20$ 3.33 1-5$ Credit card Street-hail 8.42 <10 minutes 14.18 11-20 mph null null 01-01-2023 0.45 Weekend Midnight Standard rate 75 Manhattan East Harlem South 148 Manhattan Lower East Side 1 7.08 7-10 miles 30.3 21-40$ 3.0 1-5$ Credit card Street-hail 18.98 11-20 minutes 22.38 21-30 mph null null 01-01-2023 0.30 Weekend Midnight Standard rate 66 Brooklyn DUMBO/Vinegar Hill 255 Brooklyn Williamsburg (North Side) 1 3.23 3-6 miles 17.7 <20$ 4.04 1-5$ Credit card Street-hail 11.57 11-20 minutes 16.75 11-20 mph null null 01-01-2023 1.18 Weekend Midnight Standard rate 255 Brooklyn Williamsburg (North Side) 186 Manhattan Penn Station/Madison Sq West 1 5.91 3-6 miles 35.9 21-40$ 0.0 0$ Cash Street-hail 38.57 >30 minutes 9.19 <10 mph null null 01-01-2023 1.08 Weekend Midnight Standard rate 195 Brooklyn Red Hook 210 Brooklyn Sheepshead Bay 1 11.3 >10 miles 32.5 21-40$ 0.0 0$ Cash Street-hail 18.82 11-20 minutes 36.03 >30 mph null null 01-01-2023 0.19 Weekend Midnight Negotiated fare 83 Queens Elmhurst/Maspeth 129 Queens Jackson Heights 1 1.3 <2 miles 15.0 <20$ 0.0 0$ Credit card Dispatch 8.87 <10 minutes 8.79 <10 mph null null 01-01-2023 1.17 Weekend Midnight Standard rate 97 Brooklyn Fort Greene 68 Manhattan East Chelsea 1 8.28 7-10 miles 44.3 41-60$ 5.0 1-5$ Credit card Street-hail 42.4 >30 minutes 11.72 11-20 mph null null 01-01-2023 0.42 Weekend Midnight Standard rate 7 Queens Astoria 260 Queens Woodside 1 2.02 3-6 miles 12.8 <20$ 0.0 0$ Cash Street-hail 11.28 

In [0]:
# 11. Get average tip amount by day of the week
# TODO: Write the code to answer the above question
df_transformed = df.withColumn("lpep_pickup_datetime", to_timestamp(df["lpep_pickup_datetime"], "dd-MM-yyyy H.mm"))
df_transformed = df_transformed.withColumn("day_of_week", date_format(df_transformed["lpep_pickup_datetime"], "EEEE"))
display(df_transformed.limit(10))
display(df_transformed.groupBy('day_of_week').agg(avg('tip_amount').alias("Avg Tip Amount")))

lpep_pickup_datetime lpep_dropoff_datetime day_category pickup_time RatecodeID PULocationID PUBorough PUZone DOLocationID DOBorough DOZone passenger_count trip_distance distance_bins fare_amount fare_amount_bins tip_amount tip_amount_bins payment_type trip_type trip_duration duration_bins speed speed_bins day_of_week 2023-01-01T00:26:00.000+0000 01-01-2023 0.37 Weekend Midnight Standard rate 166 Manhattan Morningside Heights 143 Manhattan Lincoln Square West 1 2.58 3-6 miles 14.9 <20$ 4.03 1-5$ Credit card Street-hail 11.02 11-20 minutes 14.05 11-20 mph Sunday 2023-01-01T00:51:00.000+0000 01-01-2023 0.57 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 43 Manhattan Central Park 1 1.81 <2 miles 10.7 <20$ 2.64 1-5$ Credit card Street-hail 6.77 <10 minutes 16.04 11-20 mph Sunday 2023-01-01T00:13:00.000+0000 01-01-2023 0.19 Weekend Midnight Standard rate 41 Manhattan Central Harlem 238 Manhattan Upper West Side North 1 1.3 <2 miles 6.5 <20$ 1.7 1-5$ Credit card Street-hail 5.82 <10 minutes 13.4 11-20 mph Sunday 2023-01-01T00:33:00.000+0000 01-01-2023 0.39 Weekend Midnight Standard rate 41 Manhattan Central Harlem 74 Manhattan East Harlem North 1 1.1 <2 miles 6.0 <20$ 0.0 0$ Credit card Street-hail 5.97 <10 minutes 11.06 11-20 mph Sunday 2023-01-01T00:53:00.000+0000 01-01-2023 1.11 Weekend Midnight Standard rate 41 Manhattan Central Harlem 262 Manhattan Yorkville East 1 2.78 3-6 miles 17.7 <20$ 0.0 0$ Cash Street-hail 17.55 11-20 minutes 9.5 <10 mph Sunday 2023-01-01T00:09:00.000+0000 01-01-2023 0.26 Weekend Midnight Standard rate 181 Brooklyn Park Slope 45 Manhattan Chinatown 2 3.8 3-6 miles 19.1 <20$ 4.85 1-5$ Credit card Street-hail 17.42 11-20 minutes 13.09 11-20 mph Sunday 2023-01-01T00:11:00.000+0000 01-01-2023 0.24 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 75 Manhattan East Harlem South 1 1.88 <2 miles 14.2 <20$ 0.0 0$ Cash Street-hail 12.95 11-20 minutes 8.71 <10 mph Sunday 2023-01-01T00:41:00.000+0000 01-01-2023 0.46 Weekend Midnight Standard rate 41 Manhattan Central Harlem 166 Manhattan Morningside Heights 2 1.11 <2 miles 7.2 <20$ 1.0 1-5$ Credit card Street-hail 4.95 <10 minutes 13.45 11-20 mph Sunday 2023-01-01T00:50:00.000+0000 01-01-2023 1.13 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 140 Manhattan Lenox Hill East 1 4.22 3-6 miles 24.7 21-40$ 3.0 1-5$ Credit card Street-hail 23.17 21-30 minutes 10.93 11-20 mph Sunday 2023-01-01T00:16:00.000+0000 01-01-2023 0.41 Weekend Midnight Standard rate 255 Brooklyn Williamsburg (North Side) 234 Manhattan Union Sq 2 4.8 3-6 miles 26.8 21-40$ 0.0 0$ Credit card Street-hail 25.52 21-30 minutes 11.29 11-20 mph Sunday

day_of_week Avg Tip Amount Wednesday 2.2478791700103176 Tuesday 2.2151681133393217 Friday 2.2320303200449203 Thursday 2.315743324909351 Saturday 2.264348570675801 Monday 2.2160215900146194 Sunday 2.3455722326454023

In [0]:
# 12. Get average tip amount by hour of the day
# TODO: Write the code to answer the above question
df_hour = df.withColumn("lpep_pickup_datetime", to_timestamp(df["lpep_pickup_datetime"], "dd-MM-yyyy H.mm"))
df_hour = df_hour.withColumn("pickup_hour", hour(df_hour["lpep_pickup_datetime"]))
display(df_hour.limit(10))

display(df_hour.groupBy('pickup_hour').agg(avg('tip_amount').alias('Avg Tip Amount')))

lpep_pickup_datetime lpep_dropoff_datetime day_category pickup_time RatecodeID PULocationID PUBorough PUZone DOLocationID DOBorough DOZone passenger_count trip_distance distance_bins fare_amount fare_amount_bins tip_amount tip_amount_bins payment_type trip_type trip_duration duration_bins speed speed_bins pickup_hour 2023-01-01T00:26:00.000+0000 01-01-2023 0.37 Weekend Midnight Standard rate 166 Manhattan Morningside Heights 143 Manhattan Lincoln Square West 1 2.58 3-6 miles 14.9 <20$ 4.03 1-5$ Credit card Street-hail 11.02 11-20 minutes 14.05 11-20 mph 0 2023-01-01T00:51:00.000+0000 01-01-2023 0.57 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 43 Manhattan Central Park 1 1.81 <2 miles 10.7 <20$ 2.64 1-5$ Credit card Street-hail 6.77 <10 minutes 16.04 11-20 mph 0 2023-01-01T00:13:00.000+0000 01-01-2023 0.19 Weekend Midnight Standard rate 41 Manhattan Central Harlem 238 Manhattan Upper West Side North 1 1.3 <2 miles 6.5 <20$ 1.7 1-5$ Credit card Street-hail 5.82 <10 minutes 13.4 11-20 mph 0 2023-01-01T00:33:00.000+0000 01-01-2023 0.39 Weekend Midnight Standard rate 41 Manhattan Central Harlem 74 Manhattan East Harlem North 1 1.1 <2 miles 6.0 <20$ 0.0 0$ Credit card Street-hail 5.97 <10 minutes 11.06 11-20 mph 0 2023-01-01T00:53:00.000+0000 01-01-2023 1.11 Weekend Midnight Standard rate 41 Manhattan Central Harlem 262 Manhattan Yorkville East 1 2.78 3-6 miles 17.7 <20$ 0.0 0$ Cash Street-hail 17.55 11-20 minutes 9.5 <10 mph 0 2023-01-01T00:09:00.000+0000 01-01-2023 0.26 Weekend Midnight Standard rate 181 Brooklyn Park Slope 45 Manhattan Chinatown 2 3.8 3-6 miles 19.1 <20$ 4.85 1-5$ Credit card Street-hail 17.42 11-20 minutes 13.09 11-20 mph 0 2023-01-01T00:11:00.000+0000 01-01-2023 0.24 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 75 Manhattan East Harlem South 1 1.88 <2 miles 14.2 <20$ 0.0 0$ Cash Street-hail 12.95 11-20 minutes 8.71 <10 mph 0 2023-01-01T00:41:00.000+0000 01-01-2023 0.46 Weekend Midnight Standard rate 41 Manhattan Central Harlem 166 Manhattan Morningside Heights 2 1.11 <2 miles 7.2 <20$ 1.0 1-5$ Credit card Street-hail 4.95 <10 minutes 13.45 11-20 mph 0 2023-01-01T00:50:00.000+0000 01-01-2023 1.13 Weekend Midnight Standard rate 24 Manhattan Bloomingdale 140 Manhattan Lenox Hill East 1 4.22 3-6 miles 24.7 21-40$ 3.0 1-5$ Credit card Street-hail 23.17 21-30 minutes 10.93 11-20 mph 0 2023-01-01T00:16:00.000+0000 01-01-2023 0.41 Weekend Midnight Standard rate 255 Brooklyn Williamsburg (North Side) 234 Manhattan Union Sq 2 4.8 3-6 miles 26.8 21-40$ 0.0 0$ Credit card Street-hail 25.52 21-30 minutes 11.29 11-20 mph 0

pickup_hour Avg Tip Amount 12 2.1704932330827065 22 2.296056173200701 1 2.3185490196078433 13 2.1371298664393312 6 2.2759126539753636 16 2.3640042826552468 3 2.0483297644539613 20 2.2891566265060233 5 2.6510364145658265 19 2.2730761154855625 15 2.070241016652058 9 2.2785714285714302 17 2.4087332908975174 4 2.469189189189189 8 2.372155082081732 23 2.174083457526081 7 2.1973406500633175 10 2.201853461657871 21 2.2341086350974937 11 2.2392328684050935 14 2.1894724711907805 2 2.3138560885608856 0 2.0187109768378653 18 2.405711318795431

In [0]:
# 13. Calculate tip amount per mile and describe its statistics
# TODO: Write the code to answer the above question
df_tippermile = df.withColumn(
    'tip_per_mile',
    when(col('trip_distance') > 0, col('tip_amount') / col('trip_distance')).otherwise(None)
)
display(df_tippermile.select('tip_per_mile').describe())

summary tip_per_mile count 60698 mean 0.9462572701376127 stddev 0.9968029260390485 min 0.0 max 17.857142857142858

In [0]:
# 14. Get records with invalid fare or tip amounts. Then remove these invalid records from dataframe (make it clean)
# TODO: Write the code to answer the above question
display(df.filter(col('fare_amount').isNull() | col('tip_amount').isNull() ))


lpep_pickup_datetime lpep_dropoff_datetime day_category pickup_time RatecodeID PULocationID PUBorough PUZone DOLocationID DOBorough DOZone passenger_count trip_distance distance_bins fare_amount fare_amount_bins tip_amount tip_amount_bins payment_type trip_type trip_duration duration_bins speed speed_bins

In [0]:
# 15. Calculate average tip by trip_duration
# TODO: Write the code to answer the above question
display(df.groupBy('trip_duration').agg(avg('tip_amount')))

trip_duration avg(tip_amount) 19.98 3.4456521739130435 12.32 1.9217857142857144 13.4 2.153953488372093 17.52 2.5034375 9.13 1.4236507936507936 15.5 3.039285714285714 17.95 3.054166666666667 14.9 2.6412500000000003 10.65 1.7689062500000001 26.72 2.5175 26.7 2.125 45.43 0.0 35.17 4.802 9.55 1.6949333333333332 15.92 3.20448275862069 16.75 2.1162500000000004 19.27 2.2665217391304346 39.42 0.0 15.4 2.2451923076923075 24.42 3.337142857142857 37.23 3.0 9.72 1.4512345679012346 18.62 2.2134615384615386 18.78 3.080416666666667 38.93 13.71 14.18 2.1985106382978725 24.03 4.825 8.73 1.563220338983051 14.75 1.8883333333333334 18.88 2.4007692307692303 28.23 4.3525 5.05 1.3328 11.53 1.9428846153846153 21.52 2.5800000000000005 5.78 1.1878571428571427 31.03 0.0 29.47 1.9766666666666666 21.72 3.689230769230769 36.27 0.0 10.82 2.2274999999999996 8.0 1.8792039800995024 22.83 2.643076923076923 14.68 2.606470588235294 10.2 1.5543835616438355 5.13 1.5814666666666666 5.48 1.2379032258064515 25.1 2.6775 18.57 3.3333333333333335 28.08 5.21 15.7 1.7708823529411768 27.53 5.397142857142858 29.15 2.07 55.87 0.0 2.82 1.0191666666666668 32.37 3.3379999999999996 38.68 1.4066666666666665 55.43 0.0 46.22 4.0 8.92 1.4545 12.03 2.1189473684210527 18.3 3.32 15.62 2.2562857142857147 13.05 1.8253658536585367 8.43 1.4198387096774194 14.07 2.2065714285714284 20.38 2.840909090909091 21.15 2.914117647058823 47.27 10.55 25.77 4.801875 26.08 2.8114285714285714 44.58 10.27 24.7 3.015833333333333 29.42 7.471428571428571 32.3 2.416 49.87 2.325 31.22 5.6499999999999995 76.27 0.0 20.35 1.8284848484848486 8.83 1.2179365079365079 6.17 1.2131111111111108 4.88 1.0766666666666664 15.27 2.6140000000000003 8.75 1.6758181818181819 30.73 6.015 46.08 9.2 26.28 2.18125 29.93 3.2640000000000002 35.38 3.6 31.25 2.988571428571429 30.97 7.639999999999999 112.02 0.0 33.68 1.4157142857142857 10.23 1.5820454545454545 31.98 1.425 23.35 2.5 4.92 1.1121951219512196 14.87 1.5003125000000002 9.77 1.3478124999999999 17.33 3.408823529411765 3.02 0.9099999999999999 23.67 4.777272727272727 32.05 4.404 29.77 3.6325000000000003 31.15 3.78 11.45 1.8575000000000002 34.02 2.0 18.03 3.9122222222222223 20.77 3.8570370370370375 37.68 7.703333333333333 49.17 12.0 17.9 2.1792307692307693 45.63 0.0 7.42 1.2986486486486486 11.4 2.294318181818182 14.05 2.772448979591837 16.6 2.957857142857143 28.32 3.59 5.4 1.3863414634146343 6.27 1.3875409836065573 4.23 1.42475 45.87 0.125 23.8 4.1466666666666665 39.75 3.74 2.55 0.75 29.83 8.905000000000001 27.48 6.7128571428571435 61.98 0.0 7.0 1.6901025641025638 15.43 2.1791176470588236 4.02 0.768695652173913 12.82 2.209811320754717 6.43 1.2306557377049179 28.22 4.167142857142857 23.95 4.365333333333334 32.67 3.2980000000000005 21.55 3.2864999999999993 15.9 2.671724137931035 8.97 1.6406451612903226 8.48 1.7036923076923078 20.17 2.733913043478261 15.48 2.94125 24.78 3.019230769230769 65.27 22.98 44.05 9.633333333333333 21.42 3.521052631578947 28.57 3.4766666666666666 24.9 4.346 26.38 2.974 12.43 2.1767441860465118 11.5 1.796896551724138 11.35 2.099473684210526 12.85 2.2277419354838712 3.57 1.0019047619047619 4.93 1.1971428571428573 12.93 2.7974999999999994 68.88 0.0 37.4 6.9437500000000005 20.53 3.3745454545454545 44.08 0.0 18.82 3.4492307692307693 23.12 2.9343749999999997 22.05 2.8375000000000004 3.5 1.5753846153846154 16.13 3.1707317073170733 24.07 3.656666666666667 11.42 1.8912499999999999 27.45 5.29875 16.73 2.696896551724138 31.7 7.132499999999999 25.63 1.8199999999999998 36.2 3.0 41.6 6.78 9.5 1.931551724137931 6.37 1.572982456140351 6.1 1.077457627118644 17.53 2.9917857142857143 17.58 2.841842105263158 10.25 1.54765625 2.28 0.3514285714285714 29.37 6.517142857142858 21.07 2.295625 33.18 1.0 29.78 6.622 11.6 1.745 10.73 1.7260714285714285 11.27 2.218604651162791 49.7 6.525 28.73 3.2 3.33 0.98125 49.33 0.0 43.82 5.195 8.55 1.6135849056603775 12.78 1.347857142857143 17.15 2.9560000000000004 24.25 3.548 3.88 1.11125 11.08 1.7279545454545455 19.55 3.7681250000000004 27.35 6.41777

In [0]:
# 16. Get average tip amount per hour. Show graph as visualization
# TODO: Write the code to answer the above question
display(df_hour.groupBy('pickup_hour').agg(avg('tip_amount').alias('Avg Tip Amount')))

pickup_hour Avg Tip Amount 12 2.1704932330827065 22 2.296056173200701 1 2.3185490196078433 13 2.1371298664393312 6 2.2759126539753636 16 2.3640042826552468 3 2.0483297644539613 20 2.2891566265060233 5 2.6510364145658265 19 2.2730761154855625 15 2.070241016652058 9 2.2785714285714302 17 2.4087332908975174 4 2.469189189189189 8 2.372155082081732 23 2.174083457526081 7 2.1973406500633175 10 2.201853461657871 21 2.2341086350974937 11 2.2392328684050935 14 2.1894724711907805 2 2.3138560885608856 0 2.0187109768378653 18 2.405711318795431

Databricks visualization. Run in Databricks to view.

In [0]:
# 17. Get average tip by passenger count and display as bar chart
# TODO: Write the code to answer the above question
display(df.groupBy('passenger_count').agg(avg('tip_amount')))

passenger_count avg(tip_amount) 3 2.309636576787808 1 2.2478845308828332 >3 2.434799190010125 2 2.2726701916721734

Databricks visualization. Run in Databricks to view.

In [0]:
# 18. Get fare vs tip values and display scatter plot style visualization
# TODO: Write the code to answer the above question
display(df.groupBy('fare_amount').agg(sum('tip_amount')))

fare_amount sum(tip_amount) 14.9 4008.1599999999935 15.5 92.25 72.3 74.82000000000001 8.0 153.5 70.0 1323.2000000000003 24.7 1501.8900000000008 49.9 133.37 46.4 227.72 11.4 4278.19 7.0 147.33999999999997 76.5 23.8 11.5 137.69 31.7 1108.1699999999998 70.2 26.0 71.6 50.209999999999994 9.5 139.32 43.6 290.76 74.4 33.87 42.9 371.51 26.87 9.23 20.5 2350.38 103.1 0.0 68.8 42.209999999999994 31.5 13.85 97.5 0.0 12.5 130.84999999999997 4.5 21.369999999999997 27.06 2.62 89.5 0.0 26.8 1357.7599999999998 65.3 62.46 26.1 1467.0299999999995 101.0 8.88 29.0 12.75 40.5 8.85 33.1 904.0400000000002 75.0 164.0 57.6 133.46999999999997 47.0 0.0 24.5 55.790000000000006 42.0 0.0 6.5 1714.0600000000022 17.7 3418.6399999999994 21.2 2296.4500000000007 35.0 59.54 51.3 252.51 18.0 84.62000000000002 80.0 73.31 79.3 21.84 81.4 0.0 16.5 59.75 12.8 4357.929999999991 133.9 0.0 33.5 14.1 8.49 0.0 63.5 0.0 2.5 0.0 34.5 857.3 39.0 19.76 87.7 18.39 25.4 1415.3700000000003 45.5 20.520000000000003 35.9 640.6099999999999 17.5 49.019999999999996 18.4 2941.4099999999985 94.0 20.1 12.1 4236.980000000009 18.5 88.09 26.85 2.61 114.0 0.0 19.1 2944.4999999999977 25.91 3.21 75.1 59.44 37.0 8.3 34.0 22.830000000000002 89.8 0.0 14.2 4268.680000000009 25.0 101.24000000000001 64.6 56.09 54.8 140.93 118.2 0.0 46.5 5.0 61.1 73.83000000000001 63.9 79.2 28.9 1436.85 8.6 3901.219999999994 9.3 4209.110000000011 27.5 1468.5300000000007 84.9 48.650000000000006 75.8 49.0 7.5 123.89999999999998 4.0 0.0 67.4 108.69 22.5 43.959999999999994 56.9 89.97000000000001 59.7 148.28 30.5 21.54 10.8 2.22 23.0 28.53 50.0 439.35999999999996 49.2 293.66 48.5 166.13 154.9 0.0 14.5 79.83999999999999 54.1 93.69 26.34 2.57 33.8 880.7200000000001 45.0 457.54999999999995 38.7 737.31 19.8 2561.489999999997 42.5 2.75 5.1 89.80999999999999 37.5 6.19 73.7 15.0 106.6 0.0 32.5 17.11 44.3 423.81 35.2 861.9399999999998 60.4 77.86 14.7 0.0 31.0 1062.2000000000003 56.2 113.83 123.8 0.0 11.0 247.00000000000006 7.9 3328.680000000005 23.5 25.5 58.0 0.01 10.7 4475.590000000022 29.62 3.01 53.4 94.46000000000001 80.7 41.31 13.5 4260.599999999997 21.0 43.510000000000005 8.5 144.17 72.0 16.91 14.0 88.53 41.5 519.29 45.7 346.82 30.3 1284.0600000000004 29.6 1273.9199999999996 33.34 14.73 48.0 0.0 58.3 120.1 18.2 0.0 22.0 41.5 68.1 122.52 60.0 41.05 7.2 2297.9200000000037 66.0 63.510000000000005 5.15 0.0 84.2 0.0 47.8 152.16 70.9 62.559999999999995 22.6 1882.0199999999995 36.5 16.92 19.0 59.21 66.7 35.5 40.1 516.21 52.7 116.25999999999999 50.6 73.05 59.0 146.26999999999998 77.2 83.44999999999999 8.08 2.0999999999999996 77.9 17.0 39.4 595.73 96.1 19.52 37.3 679.6600000000001 28.0 11.21 122.7 0.0 19.5 54.489999999999995 87.0 0.0 24.23 2.4 17.0 3289.9600000000014 30.75 0.0 79.5 0.0 21.9 2008.1600000000008 36.6 797.3700000000001 69.5 49.7 82.1 16.72 21.5 47.65 28.46 2.92 38.0 572.48 27.0 24.34 110.1 28.57 95.4 10.0 10.0 4451.089999999983 26.5 0.0 73.0 73.18 30.0 79.96 40.0 130.42000000000002 13.0 112.12 121.7 33.94 20.07 1.82 95.0 0.0 85.6 0.0 61.8 26.92 89.1 0.0 126.2 0.0 24.6 6.68 6.0 57.42 97.2 21.99 20.0 207.85 28.2 1387.38 52.0 188.66000000000003 25.5 26.25 32.0 0.0 15.0 128.96000000000004 5.0 36.81 24.0 1910.2799999999995 32.4 1021.33 62.5 37.95 16.3 3333.8299999999963 52.17 33.07 15.6 3622.0500000000015 10.5 133.2 55.5 108.06 5.8 698.6799999999998 9.0 169.37000000000006 26.0 19.970000000000002 65.0 36.0 5.5 84.53 40.8 515.5799999999999 16.0 80.87 12.0 140.53 63.2 108.05 23.3 1752.7099999999991 47.1 156.90999999999997 161.2 32.54 78.6 24.03 42.2 422.71000000000004 47.5 0.0 96.8 0.0 83.5 5.0 140.2 10.0 38.5 9.72 29.97 9.23 44.5 10.41 49.0 0.0 90.5 19.15 91.9 0.0 44.0 10.31 23.86 1.92 120.0 0.0 42.3 3.8 26.33 5.369999999999999 24.2 1.97 36.0 16.1 41.0 8.46 15.2 0.0 35.5 16.46 85.0 19.06 8.9 5.0 122.4 15.94 15.04 1.43 16.26 5.52 27.65 2.67 68.0 2.0 46.0 0.0 13.6 0.0 29.5 6.61 28.5 27.009999999999998 57.0 11.6 11.13 0.0 24.48 2.42 26.23 11.56 82.8 0.0 100.0 21.3 16.06 1.71 55.0 58.2 15.85 6.02 39.7 5.45 125.2 30.29 43.0 10.0 17.5

Databricks visualization. Run in Databricks to view.